In [1]:
import os
from pathlib import Path
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.spatial.distance import cdist
from local_functions import *

In [2]:
main_dir = Path(os.getcwd())
data_path = main_dir / "data"

In [3]:
df_players = pd.read_csv(f'{data_path}/players.csv')
df_games = pd.read_csv(f'{data_path}/games.csv')
df_tackles = pd.read_csv(f'{data_path}/tackles.csv')
df_plays = pd.read_csv(f'{data_path}/plays.csv')
df_tracking = pd.read_csv(f'{data_path}/tracking_week_5.csv')

In [4]:
df_tracking = df_tracking.merge(df_players.loc[:, ['nflId', 'position']], on='nflId', how='left')
df_tracking['game_play_id'] = df_tracking['gameId'].astype(str) + "_" + df_tracking['playId'].astype(str)
df_tracking = df_tracking.merge(df_plays.loc[:, ['gameId', 'playId', 'ballCarrierId']], left_on=['gameId','playId','nflId'], right_on=['gameId','playId','ballCarrierId'], how='left')
df_tracking['is_ballcarrier'] = df_tracking['nflId'] == df_tracking['ballCarrierId']

In [5]:
df_tracking['x_std'] = np.where(df_tracking['playDirection'] == 'left', 120 - df_tracking['x'], df_tracking['x'])
df_tracking['y_std'] = np.where(df_tracking['playDirection'] == 'left', 160/3 - df_tracking['y'], df_tracking['y'])

In [6]:
# df_tracking['dir_std1'] = np.where((df_tracking['playDirection'] == 'left') & (df_tracking['dir'] < 90), df_tracking['dir'] + 360, df_tracking['dir'])
# df_tracking['dir_std1'] = np.where((df_tracking['playDirection'] != 'left') & (df_tracking['dir'] > 270), df_tracking['dir'] - 360, df_tracking['dir_std1'])
# df_tracking['dir_std2'] = np.where(df_tracking['playDirection'] == 'left', df_tracking['dir_std1'] - 180, df_tracking['dir_std1'])

In [7]:
# df_tracking['o_std'] = np.where((df_tracking['playDirection'] == 'left') & (df_tracking['o'] < 90), df_tracking['o'] + 360, df_tracking['o'])
# df_tracking['o_std'] = np.where((df_tracking['playDirection'] != 'left') & (df_tracking['o'] > 270), df_tracking['o'] - 360, df_tracking['o_std'])
# df_tracking['o_std'] = np.where(df_tracking['playDirection'] == 'left', df_tracking['o_std'] - 180, df_tracking['o_std'])

In [8]:
df_tracking['o_std'] = np.where(df_tracking['playDirection'] == 'left', df_tracking['o'] + 180, df_tracking['o'])
df_tracking['o_std'] = np.where(df_tracking['o_std'] > 360, df_tracking['o_std'] - 360, df_tracking['o_std'])
df_tracking['o_rad'] = np.radians(df_tracking['o_std'])
df_tracking['o_x'] = np.sin(df_tracking['o_rad'])
df_tracking['o_y'] = np.cos(df_tracking['o_rad'])

In [9]:
df_tracking['dir_std'] = np.where(df_tracking['playDirection'] == 'left', df_tracking['dir'] + 180, df_tracking['dir'])
df_tracking['dir_std'] = np.where(df_tracking['dir_std'] > 360, df_tracking['dir_std'] - 360, df_tracking['dir_std'])
df_tracking['dir_rad'] = np.radians(df_tracking['dir_std'])
df_tracking['dir_x'] = np.sin(df_tracking['dir_rad'])
df_tracking['dir_y'] = np.cos(df_tracking['dir_rad'])

In [10]:
df_tracking['s_x'] = df_tracking['dir_x'] * df_tracking['s']
df_tracking['s_y'] = df_tracking['dir_y'] * df_tracking['s']

df_tracking['a_x'] = df_tracking['dir_x'] * df_tracking['a']
df_tracking['a_y'] = df_tracking['dir_y'] * df_tracking['a']

In [30]:
df_tracking.dtypes

gameId              int64
playId              int64
nflId             float64
displayName        object
frameId             int64
time               object
jerseyNumber      float64
club               object
playDirection      object
x                 float64
y                 float64
s                 float64
a                 float64
dis               float64
o                 float64
dir               float64
event              object
position           object
game_play_id       object
ballCarrierId     float64
is_ballcarrier       bool
x_std             float64
y_std             float64
o_std             float64
o_rad             float64
o_x               float64
o_y               float64
dir_std           float64
dir_rad           float64
dir_x             float64
dir_y             float64
s_x               float64
s_y               float64
a_x               float64
a_y               float64
dtype: object

In [21]:
df_bc_frames = df_tracking[df_tracking['is_ballcarrier']].drop_duplicates(['gameId','playId','frameId','nflId']).loc[:,['gameId', 'playId', 'frameId', 'nflId', 'x_std', 'y_std', 'dir_std', 'o_std', 's', 'a']].reset_index(drop=True)

In [31]:
df_tracking = df_tracking.merge(df_bc_frames.drop('nflId', axis=1), on = ['gameId','playId','frameId'], how = 'inner', suffixes = ('', '_bc'))

In [70]:
df_tracking = calc_angle_diff(input_df = df_tracking, 
                              xc = 'x_std', 
                              yc = 'y_std', 
                              anglec = 'o', 
                              xc_ref = 'x_std_bc', 
                              yc_ref = 'y_std_bc', 
                              new_name_suffix = 'bc')

In [72]:
df_tracking = calc_angle_diff(input_df = df_tracking, 
                              xc = 'x_std', 
                              yc = 'y_std', 
                              anglec = 'dir', 
                              xc_ref = 'x_std_bc', 
                              yc_ref = 'y_std_bc', 
                              new_name_suffix = 'bc')

In [74]:
ex_gameId = df_games[(df_games['homeTeamAbbr']=='BAL') & (df_games['visitorTeamAbbr']=='CIN')]['gameId'].iloc[0]

ex_playId = df_plays[(df_plays['gameId'] == ex_gameId) & 
                     (df_plays['quarter'] == 1) &
                     (df_plays['gameClock'] == '12:57')]['playId'].iloc[0]

ex_game_play_id = str(ex_gameId) + '_' + str(ex_playId)

In [ ]:
ex_game_play_id = '2022100913_172'
#ex_game_play_id = '2022100913_55'

In [63]:
animate_tracking_data(tracking_df = df_tracking, 
                      id_game_play = ex_game_play_id,
                      x_col = 'x_std',
                      y_col = 'y_std',
                      dir_col = 'dir_std',
                      dir_arrow_metric = 's',
                      o_col = 'o_std')

['BAL' 'CIN']


In [ ]:
# pos_start = list(df_all_plays.columns).index("pos_unique") + 1
# positions = df_all_plays.columns[pos_start:]